# Sheet

# Factories

In [9]:
interface A{
    val body: String
}

class B(override val body: String): A{
    override fun toString() = "$body B"
}

class C(override val body: String): A{
    override fun toString() = "$body C"
}

fun print(obj: A){
    println(obj)
}

In [10]:
print(C("My body"))

My body C


In [14]:
interface AFactory<out T: A>{
    fun create(body: String): T
}

object BFactory: AFactory<B>{
    override fun create(body: String): B = B(body)
}

fun <T: A> createWithAWord(word: String, factory: AFactory<T>) = factory.create("Word: $word")

In [15]:
createWithAWord("Hello", BFactory)

Word: Hello B

In [17]:
fun <T: A> createWithAWord(word: String, factoryFunction: (String) -> T) = factoryFunction("Word: $word")

In [19]:
createWithAWord("Hello", ::B)

Word: Hello B

In [21]:
createWithAWord("Hello"){body -> B(">\t$body")}

>	Word: Hello B

# Factory functions

In [2]:
data class Client(val url: String)

interface Request{
    val client: Client
}

data class RequestImpl(override val client: Client): Request{
//    constructor(url: String): this(Client(url))
}

In [4]:
fun Request(url: String): Request{
    return RequestImpl(Client(url))
}

In [5]:
Request("DDD")

RequestImpl(client=Client(url=DDD))

In [33]:
listOf(1,2,3)

[1, 2, 3]

# Lazy

In [12]:
class WithLazy{
    val prop = 2
        get(){
            println("Hit $field")
            return field
        }

    val lazyProp by lazy{
        println("Hit lazy")
        2
    }
}

In [13]:
val withLazy = WithLazy()

In [14]:
withLazy.prop
withLazy.prop
withLazy.prop

Hit 2
Hit 2
Hit 2


2

In [15]:
withLazy.lazyProp
withLazy.lazyProp
withLazy.lazyProp

Hit lazy


2

# Builder

In [7]:
data class Buildable(
    var a: Int = 1,
    var b: Int = 2,
    var c: Int = 3
){
    fun setABC(value: Int){
        a = value
        b = value
        c = value
    }
}

// Buildable.builder()
//     .setA(1)
//     .setB(2)
//     .setC(3)
//     .setABC(1)
//     .build()

In [8]:
Buildable(b = 5)

Buildable(a=1, b=5, c=3)

In [9]:
Buildable().apply { 
    a = 1
    setABC(a + b + c)
}

Buildable(a=6, b=6, c=6)

In [11]:
fun Buildable(block: Buildable.()-> Unit): Buildable = Buildable().apply(block)

Buildable{ 
    a = 1
    setABC(a + b + c)
}

Buildable(a=6, b=6, c=6)

# Multiton

In [16]:
class Multiton private constructor(val name: String){
    init{
        println("Multiton $name created")
    }
    
    companion object {
        private val cache = HashMap<String, Multiton>()

        fun resolve(name: String) = cache.getOrPut(name){Multiton(name)}
    }
}

In [17]:
Multiton.resolve("a")
Multiton.resolve("a")
Multiton.resolve("b")
Multiton.resolve("a")

Multiton a created
Multiton b created


Line_61_jupyter$Multiton@5271dd0f

In [18]:
Multiton("v")

Line_67.jupyter.kts (1:1 - 9) Cannot access '<init>': it is private in 'Multiton'

Syntax Error: Syntax Error: Cannot access '<init>': it is private in 'Multiton'

In [24]:
sealed interface SealedMultiton{
    object A: SealedMultiton
    object B: SealedMultiton
    class Custom(val body: String): SealedMultiton
}

fun evaluateSealedMultiton(sealed: SealedMultiton) = when(sealed){
    is SealedMultiton.A-> println("A")
    is SealedMultiton.B-> println("B")
    is SealedMultiton.Custom -> println(sealed.body)
}

# Adapter

In [25]:
val array = doubleArrayOf(1.0,2.0)
val list = listOf(1.0,2.0)


fun consumeList(l: List<Double>){
    println(l)
}

fun convertArrayToList(array: DoubleArray): List<Double> = array.asList()//List(array.size){i -> array[i]}

consumeList(convertArrayToList(array))

[1.0, 2.0]


# Decorator?

In [27]:
@JvmInline
value class EMail(val address: String)

fun EMail.validate(): Boolean = TODO()

val EMail.server get() = address.substringAfter("@")

# Delegate

In [28]:
class ValueHolder{
    var value = 2

    fun printValue(){
        println(value)
    }
}

ValueHolder().apply { value = 6 }.printValue()

6


Bad example

In [29]:
class ModifiedValueHolder: ValueHolder(){
    override fun printValue(){
        print("value = ")
        super.printValue()
    }
}

ModifiedValueHolder().apply { value = 6 }.printValue()

Line_141.jupyter.kts (1:28 - 39) This type is final, so it cannot be inherited from
Line_141.jupyter.kts (2:5 - 13) 'printValue' in 'ValueHolder' is final and cannot be overridden
Line_141.jupyter.kts (8:31 - 36) Unresolved reference. None of the following candidates is applicable because of receiver type mismatch: 
public final var value: Int defined in Line_141_jupyter.ModifiedValueHolder

Syntax Error: Syntax Error: This type is final, so it cannot be inherited from

In [27]:
class GoodValueHolder(val valueHolder: ValueHolder = ValueHolder()){

    var value by valueHolder::value

    fun printValue(){
        print("value = ")
        valueHolder.printValue()
    }
}
GoodValueHolder().apply { value = 6 }.printValue()

value = 6


In [ ]:
class CompositeValueHolder(
    val a: ValueHolder,
    val b: ValueHolder
){
    fun printValue(){
        print("a = ")
        a.printValue()
        println()
        print("b = ")
        a.printValue()

    }
}

In [43]:
class Id(val value: String)

In [44]:
Id("d3d").value

d3d

In [41]:
Id("fff").length

Line_154.jupyter-kts (1:11 - 17) Unresolved reference: length

Syntax Error: Syntax Error: Unresolved reference: length

# Proxy

In [30]:
class StringProxy(val string: String): CharSequence by string{
    override fun get(index: Int): Char{
        return if(index < 0)  '!' else string[index]
    }
}

In [31]:
val proxy = StringProxy("dddd")

println(proxy[0])
println(proxy[-1])

d
!


# Observer

In [1]:
class ObservableValueHolder(defaultValue: Int, val callback: (Int) -> Unit){
    var value: Int = defaultValue
        set(value){
            field = value
            callback(value)
        }
}

In [2]:
val holder = ObservableValueHolder(1){
    println("Changed value = $it")
}
holder.value = 6
holder.value = 7

Changed value = 6
Changed value = 7


# Visitor

### Classic visitor

In [13]:
interface Structure

class StringStructure(val string: String): Structure

class IntStructure(val int: Int): Structure

class StructureList(val content: List<Structure>): Structure

In [17]:
fun interface StructureVisitor{
    fun visit(structure: Structure): Unit
}

val myStructureVisitor = object: StructureVisitor{
    override fun visit(structure: Structure){
        when(structure){
            is StringStructure -> println("It is a StringStructure with value ${structure.string}")
            is IntStructure -> println("It is a IntStructure with value ${structure.int}")
            is StructureList -> structure.content.forEach{ visit(it) }
            else -> println("I don't know what it is")
        }
    }
}

fun StructureList.visit(visitor: StructureVisitor){
    visitor.visit(this)
}

In [24]:
fun List<Structure>.asStructure() = StructureList(this)

@JvmName("stringsAsStruct")
fun List<String>.asStructure() = StructureList(map{StringStructure(it)})

val structureList = StructureList(
    listOf(
        StringStructure("ddd"),
        IntStructure(2),    
        IntStructure(7),
        listOf("aaa", "bbb").asStructure()
    )
)

structureList.visit(myStructureVisitor)

It is a StringStructure with value ddd
It is a IntStructure with value 2
It is a IntStructure with value 7
It is a StringStructure with value aaa
It is a StringStructure with value bbb


### Kotlin idiomatic visiting

In [27]:
sealed interface SealedStructure

class StringSealedStructure(val string: String): SealedStructure

class IntSealedStructure(val int: Int): SealedStructure

In [28]:
fun List<SealedStructure>.visit(visitor: (SealedStructure) -> Unit){
    forEach(visitor)
}

In [30]:
val sealedStructureList = listOf<SealedStructure>(
    StringSealedStructure("ddd"),
    IntSealedStructure(2),    
    IntSealedStructure(7),
)

sealedStructureList.visit{ structure ->
    when(structure){
        is StringSealedStructure -> println("It is a StringSealedStructure with value ${structure.string}")
        is IntSealedStructure -> println("It is a IntSealedStructure with value ${structure.int}")
        else -> {} // why is that?
    }
}

Line_206.jupyter.kts (8:5 - 9) 'when' expression must be exhaustive, add necessary 'else' branch

Syntax Error: Syntax Error: 'when' expression must be exhaustive, add necessary 'else' branch

# Observer

In [8]:
import kotlin.properties.Delegates

class ObservableHolder{
    var observable: Int by Delegates.observable<Int>(1){ property, oldValue, newValue ->
        println("${property.name} $newValue")
    }
}

In [9]:
val holder = ObservableHolder()

holder.observable = 5

observable 5


In [12]:
class Response(val header: String, val body: () -> String ){
    fun onRead(callback: (String) -> Unit){
        callback(body())
    }
}

class Call(val request: String, val onResponse: (Response) -> Unit){
    fun start(){
        onResponse(Response("header"){"body"})
    }
}

Call("spc"){ response->
    println(response.header)
    response.onRead{ body->
        println(body)
    }
}.start()

header
body
